## Izračun skladnosti jadralcev in čolnov 

Povezava na bazo (eksplicitna, brez DSN)

In [17]:
import pyodbc

conn = "DRIVER={MySQL ODBC 5.3 Unicode Driver};SERVER=pb.fri.uni-lj.si;DATABASE=tup;UID=tup;PWD=tupvaje"
cnxn = pyodbc.connect(conn)
cursor = cnxn.cursor()

Na fakultetnem MariaDB strežniku imamo dostop do dveh podatkovnih baz:
* `tup`: samo za branje
* `sandbox`: vse pravice
    
Dostop: `ime_baze.ime_tabele`

In [18]:
cursor.execute("DROP TABLE IF EXISTS sandbox.optimal")
cursor.execute("CREATE TABLE sandbox.optimal ( jid INTEGER, cid INTEGER, "
               "skladnost INTEGER, PRIMARY KEY (jid));")
cursor.commit()

Izvedemo poizvedbo in prenesemo vse rezultate, ter jih obdelamo.
Alternativna rešitev: uporaba dveh kurzorjev.

In [19]:
jadralci = cursor.execute("SELECT jid FROM Jadralec").fetchall()
for jadralec in jadralci:
    result = cursor.execute(
        "SELECT cid, MOD(?+cid, 11) as skladnost FROM Coln "
        "ORDER BY skladnost DESC LIMIT 1", jadralec.jid).fetchone()
    
    jid = jadralec.jid
    cid = result.cid
    skladnost = result.skladnost

    cursor.execute("INSERT INTO sandbox.optimal VALUES (?,?,?)", jid, cid, skladnost)
    cursor.commit()

Izpis vsebine dobljene tabele `optimal`.

In [20]:
optimal = cursor.execute("SELECT * FROM sandbox.optimal")
for r in optimal:
    print (r)

(22, 104, 5)
(29, 102, 10)
(31, 104, 3)
(32, 104, 4)
(58, 104, 8)
(64, 104, 3)
(71, 104, 10)
(74, 101, 10)
(85, 101, 10)
(95, 102, 10)


Ne pozabite: ***vedno*** zapremo povezavo!

In [21]:
cnxn.close()